In [1]:
import re
import torch
from datasets import load_dataset, DatasetDict
from transformers import BertForQuestionAnswering, BertTokenizer, AutoTokenizer, pipeline

In [2]:
squad = load_dataset("squad", split="train[:5000]")
squad = squad.train_test_split(test_size=0.2)
squad

Found cached dataset squad (/Users/kaishuowang/.cache/huggingface/datasets/squad/plain_text/1.0.0/d6ec3ceb99ca480ce37cdd35555d6cb2511d223b9150cce08a837ef62ffea453)


DatasetDict({
    train: Dataset({
        features: ['id', 'title', 'context', 'question', 'answers'],
        num_rows: 4000
    })
    test: Dataset({
        features: ['id', 'title', 'context', 'question', 'answers'],
        num_rows: 1000
    })
})

In [3]:
squad['train'][0]

{'id': '56d20bf6e7d4791d00902623',
 'title': 'Frédéric_Chopin',
 'context': 'In 1817 the Saxon Palace was requisitioned by Warsaw\'s Russian governor for military use, and the Warsaw Lyceum was reestablished in the Kazimierz Palace (today the rectorate of Warsaw University). Fryderyk and his family moved to a building, which still survives, adjacent to the Kazimierz Palace. During this period, Fryderyk was sometimes invited to the Belweder Palace as playmate to the son of the ruler of Russian Poland, Grand Duke Constantine; he played the piano for the Duke and composed a march for him. Julian Ursyn Niemcewicz, in his dramatic eclogue, "Nasze Przebiegi" ("Our Discourses", 1818), attested to "little Chopin\'s" popularity.',
 'question': 'What is the title and name of the ruler whose son Chopin was friends with?',
 'answers': {'text': ['Grand Duke Constantine'], 'answer_start': [428]}}

In [12]:
tokenizer = AutoTokenizer.from_pretrained('bert-base-uncased')

def preprocess_function(examples):
    print(examples)
    questions = [q.strip() for q in examples["question"]]
    inputs = tokenizer(
        questions,
        examples["context"],
        max_length=128,
        truncation="only_second",
        return_offsets_mapping=True,
        padding="max_length",
    )

    offset_mapping = inputs.pop("offset_mapping")
    answers = examples["answers"]
    start_positions = []
    end_positions = []

    for i, offset in enumerate(offset_mapping):
        answer = answers[i]
        start_char = answer["answer_start"][0]
        end_char = answer["answer_start"][0] + len(answer["text"][0])
        sequence_ids = inputs.sequence_ids(i)

        # Find the start and end of the context
        idx = 0
        while sequence_ids[idx] != 1:
            idx += 1
        context_start = idx
        while sequence_ids[idx] == 1:
            idx += 1
        context_end = idx - 1

        # If the answer is not fully inside the context, label it (0, 0)
        if offset[context_start][0] > end_char or offset[context_end][1] < start_char:
            start_positions.append(0)
            end_positions.append(0)
        else:
            # Otherwise it's the start and end token positions
            idx = context_start
            while idx <= context_end and offset[idx][0] <= start_char:
                idx += 1
            start_positions.append(idx - 1)

            idx = context_end
            while idx >= context_start and offset[idx][1] >= end_char:
                idx -= 1
            end_positions.append(idx + 1)

    inputs["start_positions"] = start_positions
    inputs["end_positions"] = end_positions
    return inputs

In [13]:
tokenized_squad = squad.map(preprocess_function, batched=True, remove_columns=squad["train"].column_names)

Map:   0%|          | 0/4000 [00:00<?, ? examples/s]

{'id': ['56d1057217492d1400aab75e', '56cc6e346d243a140015efac', '56d12f4217492d1400aabb9b', '56cc88386d243a140015effd', '5733d88b4776f41900661345', '56cfb9bf234ae51400d9bf08', '56cd7c1962d2951400fa6621', '56ce345caab44d1400b88581', '56cef8faaab44d1400b88d6a', '5733a70c4776f41900660f65', '573404abd058e614000b67cd', '56cf1ba9aab44d1400b88d8f', '56ce31baaab44d1400b8853a', '56cf4ad1aab44d1400b88f64', '5733ca05d058e614000b6264', '56bec8a13aeaaa14008c943f', '56cffa2a234ae51400d9c1d3', '56cfb897234ae51400d9bee3', '56cedbb9aab44d1400b88b0f', '56d4bf242ccc5a1400d831be', '56cfdf7b234ae51400d9bfd6', '56d1335f17492d1400aabc15', '56beca973aeaaa14008c947b', '56d5372f2593cc1400307ae6', '56cc5f3f6d243a140015ef48', '56bfdd3fa10cfb140055134d', '56cec6e9aab44d1400b88a29', '56d004e5234ae51400d9c266', '573018d5947a6a140053d0e6', '56cec2a1aab44d1400b889e3', '56cfb7f9234ae51400d9bed8', '56becb8d3aeaaa14008c9498', '56d5324d2593cc1400307ac9', '56cbedde6d243a140015edf5', '56bec3303aeaaa14008c9393', '56cf4a29aab

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

{'id': ['56cd81df62d2951400fa6668', '56bfbf2fa10cfb14005512a4', '56d4831f2ccc5a1400d83156', '56d61a451c85041400946f10', '56cd8d2162d2951400fa66cd', '56cc52186d243a140015ef03', '56d4efd92ccc5a1400d83376', '56d114ae17492d1400aab8bb', '56ce3124aab44d1400b8852e', '56cbff116d243a140015ee4a', '56cfee5d234ae51400d9c0f9', '56cc3ad16d243a140015eedb', '573426864776f4190066197d', '56cfeb52234ae51400d9c0c0', '56cd742662d2951400fa65d6', '56cfb502234ae51400d9beb2', '56d4eaca2ccc5a1400d83347', '56cc86f26d243a140015eff5', '56d43da72ccc5a1400d830c1', '56bed1243aeaaa14008c94b4', '56cee069aab44d1400b88bbc', '56cf5674aab44d1400b8904c', '5733cd504776f41900661292', '56cd798262d2951400fa65f7', '5733adb64776f41900661004', '56d372e959d6e41400146401', '5733d88b4776f41900661346', '573404abd058e614000b67c9', '56cffcf3234ae51400d9c20d', '573382a14776f41900660c2f', '56cd8d2162d2951400fa66ce', '56d64dca1c8504140094708f', '56cf38a9aab44d1400b88e97', '56cc61346d243a140015ef70', '573383e94776f41900660c5e', '56d07aa6234

In [17]:
tokenized_squad['train']

Dataset({
    features: ['input_ids', 'token_type_ids', 'attention_mask', 'start_positions', 'end_positions'],
    num_rows: 4000
})